# Create the module list and save it into txt file

In [18]:
# 7 traits
# Sample size is 45
# 1127 images, saparated into 3 modules
# 7*45*3 modules in total

# Define traits
traits = ['dominant','warm','competent','feminine','youthful','attractive','open']

# Sample Size
sample_size = 45

# Number of modules
num_modules = 3

# Open the file for writing
with open('BackEnd_CurrentCount.txt', 'w') as file:
    # Iterate over each trait
    for trait in traits:
        # Iterate over a range of sample size
        for par_num in range(sample_size):
            # Iterate over a range of modules
            for mol_num in range(num_modules):
                module_name = '{}_Module{}-{}'.format(trait, par_num + 1, mol_num + 1)
                line = '{} {}\n'.format(module_name, 0)  # Separated by tab, followed by 0
                file.write(line)




In [1]:
import random

# Function to shuffle lines in a file
def shuffle_lines_in_file(file_path):
    # Read lines from the file
    with open(file_path, 'r') as file:
        lines = file.readlines()

    # Shuffle the lines
    random.shuffle(lines)

    # Write shuffled lines back to the file
    with open(file_path, 'w') as file:
        file.writelines(lines)


file_path = 'BackEnd_CurrentCount.txt'  
shuffle_lines_in_file(file_path)

# Assign stimuli to each module

In [2]:
# import package
import os
import random
import itertools

In [4]:
# Set the path to the folder containing the images
images_folder = "images"

# Set the path to the output folder
output_folder = "moduleStimuli"
os.makedirs(output_folder, exist_ok=True)

# Set the path to the attention check output folder
atten_check_output_folder = "attenCheckStimuli"
os.makedirs(atten_check_output_folder, exist_ok=True)

# Get a list of all image files in the images folder
image_files = [f for f in os.listdir(images_folder) if os.path.isfile(os.path.join(images_folder, f)) and f.lower().endswith(('.jpg', '.jpeg', '.png', '.gif'))]

# Shuffle the image files to randomize the assignment
random.shuffle(image_files)

FileNotFoundError: [Errno 2] No such file or directory: 'images'

In [21]:
# Define traits
traits = ['dominant','warm','competent','feminine','youthful','attractive','open']

# Number of modules
num_modules = 3

# Image number in each module
modules_size = [376,375,375]

# Sample Size for each image and trait
sample_size = 45

# Number of attantion check
num_atten = 6

# index of attention check images, start at 48th trial, and interval each 47 trials, 8 attention checks in total
index_atten = list(range(61, modules_size[0], 62))

In [22]:
index_atten

[61, 123, 185, 247, 309, 371]

In [23]:
# Find replicated images - different target person in same images
# As the images are named as originalName_v1.jpg, so we compare the originalName_v to find the same image

replicated_images = {}

for image_file in image_files:
    # Extract the key (words before the fifth-to-last character)
    if image_file[-6] == 'v':
        key = image_file[:-5]
        
        # Check if the key already exists in the replicated_images dictionary
        if key in replicated_images:
            replicated_images[key].append(image_file)
        else:
            replicated_images[key] = [image_file]

replicated_images = {key: value for key, value in replicated_images.items() if len(value) > 1}

In [24]:
# Filter out replicated images and get the retained images
replicated_images_list = [image for images_list in replicated_images.values() for image in images_list]
retained_images = [image for image in image_files if image not in replicated_images_list]

In [25]:
# Iterate over each trait
for trait in traits:
    # Iterate over a range of sample size
    for par_num in range(sample_size):

        # Create modules
        modules = [[] for _ in range(num_modules)]

        # Calculate the number of images in each module
        module_counts = [0] * num_modules

        # Create attention check image list
        atten_check_images = [[] for _ in range(num_modules)]

        # Assign replicated images into different modules
        for key, values in replicated_images.items():
            for value in values:
                # Determine the index of the module to assign the image to
                module_index = sum(module_counts) % num_modules
                # Append the image to the selected module
                modules[module_index].append(value)
                # Increment the count for the selected module
                module_counts[module_index] += 1 

        # Randomly select images from each module which will be test for attention check
        for i, mod_list in enumerate(modules):
            if len(mod_list) >= num_atten:
                atten_check_images[i] = random.sample(mod_list, num_atten)

        # Select another relative images for attention check and Store attention check images
        # Iterate for each module      
        for i, module in enumerate(atten_check_images):
            atten_check_both=[]

            # Iterate for each images to find the same image but with another target person
            for j in range(len(module)):
                atten_check_image1 = atten_check_images[i][j]
                # select another image which is the same as attention check image but with another target person
                atten_check_images_list = replicated_images[atten_check_image1[0:-5]].copy()
                atten_check_images_list.remove(atten_check_image1)
                atten_check_image2 = random.choice(atten_check_images_list)
                atten_check_both.append([atten_check_image1, atten_check_image2])

            txt_filename = os.path.join(atten_check_output_folder, f"{trait}_Module{par_num+1}-{i + 1}_attenCheck.txt")
            with open(txt_filename, 'w') as txt_file:
                for pair in atten_check_both:
                    txt_file.write(' '.join(pair) + '\n')

        # Needed image number of each module after assigning replicated images
        module_len = []

        for sublist in modules:
            module_len.append(len(sublist))

        needed_len = [size - length for size, length in zip(modules_size, module_len)]

        # Calculate the cumulative sum of needed_len
        cumulative_sum = list(itertools.accumulate(needed_len))

        # Loop through each module and append the corresponding subset of retained_images
        for i in range(len(cumulative_sum)):
            start_index = 0 if i == 0 else cumulative_sum[i-1]
            end_index = cumulative_sum[i]

            for j, image in enumerate(retained_images[start_index:end_index]):
                modules[i].append(image)
            
            random.shuffle(modules[i])

            modules[i] = [img_name for img_name in modules[i] if img_name not in atten_check_images[i]]

            for j, index in enumerate(index_atten):
                modules[i].insert(index, atten_check_images[i][j])

            # Store each module
            for i, module in enumerate(modules):
                txt_filename = os.path.join(output_folder, f"{trait}_Module{par_num+1}-{i + 1}.txt")
                with open(txt_filename, 'w') as txt_file:
                    for image in module:
                        txt_file.write(f"{image}\n")    
                        
                            